## Uczenie głębokie – przetwarzanie tekstu – laboratoria
# 3. RNN

### Podejście softmax z embeddingami na przykładzie NER

In [42]:
!pip install torch torchtext

Defaulting to user installation because normal site-packages is not writeable


In [43]:
from collections import Counter

import torch
from datasets import load_dataset
from torchtext.vocab import vocab
from tqdm.notebook import tqdm

Wczytujemy zbiór danych `conll2003` (https://huggingface.co/datasets/conll2003), który zawiera teksty oznaczone znacznikami części mowy (*POS tags*): 

In [44]:
dataset = load_dataset("conll2003")

Poiżej funkcja, która tworzy słownik (https://pytorch.org/text/stable/vocab.html).

Parametr `special` określa symbole specjalne:
* `<unk>` – nieznany token
* `<pad>` – wypełnienie
* `<bos>` – początek zdania
* `<eos>` – koniec zdania

In [45]:
def build_vocab(dataset):
    counter = Counter()
    for document in dataset:
        counter.update(document)
    return vocab(counter, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

In [46]:
v = build_vocab(dataset["train"]["tokens"])

In [47]:
itos = v.get_itos()  # mapowanie indeksów na tokeny

In [48]:
print(itos)

['<unk>', '<pad>', '<bos>', '<eos>', 'EU', 'rejects', 'German', 'call', 'to', 'boycott', 'British', 'lamb', '.', 'Peter', 'Blackburn', 'BRUSSELS', '1996-08-22', 'The', 'European', 'Commission', 'said', 'on', 'Thursday', 'it', 'disagreed', 'with', 'advice', 'consumers', 'shun', 'until', 'scientists', 'determine', 'whether', 'mad', 'cow', 'disease', 'can', 'be', 'transmitted', 'sheep', 'Germany', "'s", 'representative', 'the', 'Union', 'veterinary', 'committee', 'Werner', 'Zwingmann', 'Wednesday', 'should', 'buy', 'sheepmeat', 'from', 'countries', 'other', 'than', 'Britain', 'scientific', 'was', 'clearer', '"', 'We', 'do', "n't", 'support', 'any', 'such', 'recommendation', 'because', 'we', 'see', 'grounds', 'for', ',', 'chief', 'spokesman', 'Nikolaus', 'van', 'der', 'Pas', 'told', 'a', 'news', 'briefing', 'He', 'further', 'study', 'required', 'and', 'if', 'found', 'that', 'action', 'needed', 'taken', 'by', 'proposal', 'last', 'month', 'Farm', 'Commissioner', 'Franz', 'Fischler', 'ban', '

In [49]:
len(itos)  # liczba różnych tokenów w słowniku

23627

In [50]:
v["rejects"]  # indeks tokenu `on`

5

In [51]:
v["<unk>"]  # indeks nieznanego tokenu

0

W przypadku, gdy w analizowanym tekście znajdzie się token, którego nie ma w słowniku, będzie reprezentowany przez indeks domyślny (*default index*). Ustawiamy, żeby był taki sam, jak indeks „nieznanego tokenu”:

In [52]:
v.set_default_index(v["<unk>"])

In [53]:
def data_process(dt):
    # Wektoryzacja dokumentów tekstowych.
    return [
        torch.tensor(
            [v["<bos>"]] + [v[token] for token in document] + [v["<eos>"]],
            dtype=torch.long,
        )
        for document in dt
    ]

In [54]:
def labels_process(dt):
    # Wektoryzacja etykiet (NER)
    return [torch.tensor([0] + document + [0], dtype=torch.long) for document in dt]

Teraz wektoryzujemy wszystkie dane:

In [55]:
train_tokens_ids = data_process(dataset["train"]["tokens"])

In [56]:
test_tokens_ids = data_process(dataset["test"]["tokens"])

In [57]:
validation_tokens_ids = data_process(dataset["validation"]["tokens"])

In [58]:
train_labels = labels_process(dataset["train"]["ner_tags"])

In [59]:
validation_labels = labels_process(dataset["validation"]["ner_tags"])

In [60]:
test_labels = labels_process(dataset["test"]["ner_tags"])

Przykład, jak wyglądają dane po zwektoryzowaniu:

In [61]:
train_tokens_ids[0]

tensor([ 2,  4,  5,  6,  7,  8,  9, 10, 11, 12,  3])

In [62]:
dataset["train"][0]

{'id': '0',
 'tokens': ['EU',
  'rejects',
  'German',
  'call',
  'to',
  'boycott',
  'British',
  'lamb',
  '.'],
 'pos_tags': [22, 42, 16, 21, 35, 37, 16, 21, 7],
 'chunk_tags': [11, 21, 11, 12, 21, 22, 11, 12, 0],
 'ner_tags': [3, 0, 7, 0, 0, 0, 7, 0, 0]}

In [63]:
train_labels[0]

tensor([0, 3, 0, 7, 0, 0, 0, 7, 0, 0, 0])

Funkcja, której użyjemy do ewaluacji:

In [64]:
def get_scores(y_true, y_pred):
    # Funkcja zwraca precyzję, pokrycie i F1
    acc_score = 0
    tp = 0
    fp = 0
    selected_items = 0
    relevant_items = 0

    for p, t in zip(y_pred, y_true):
        if p == t:
            acc_score += 1

        if p > 0 and p == t:
            tp += 1

        if p > 0:
            selected_items += 1

        if t > 0:
            relevant_items += 1

    if selected_items == 0:
        precision = 1.0
    else:
        precision = tp / selected_items

    if relevant_items == 0:
        recall = 1.0
    else:
        recall = tp / relevant_items

    if precision + recall == 0.0:
        f1 = 0.0
    else:
        f1 = 2 * precision * recall / (precision + recall)

    return precision, recall, f1

Ile mamy różnych tagów NER?

In [65]:
num_tags = max([max(x) for x in dataset["train"]["ner_tags"]]) + 1
print(num_tags)

9


Implementacja rekurencyjnej sieci neuronowej LSTM:

In [66]:
class LSTM(torch.nn.Module):

    def __init__(self):
        super(LSTM, self).__init__()
        self.emb = torch.nn.Embedding(len(v.get_itos()), 100)
        self.rec = torch.nn.LSTM(100, 256, 1, batch_first=True)
        self.fc1 = torch.nn.Linear(256, num_tags)

    def forward(self, x):
        emb = torch.relu(self.emb(x))
        lstm_output, (h_n, c_n) = self.rec(emb)
        out_weights = self.fc1(lstm_output)
        return out_weights

Stworzenie modelu:

In [67]:
lstm = LSTM()

Definicja funkcji kosztu:

In [68]:
criterion = torch.nn.CrossEntropyLoss()

Definicja optymalizatora:

In [69]:
optimizer = torch.optim.Adam(lstm.parameters())

Funkcja do ewaluacji modelu:

In [70]:
def eval_model(dataset_tokens, dataset_labels, model):
    Y_true = []
    Y_pred = []
    for i in tqdm(range(len(dataset_labels))):
        batch_tokens = dataset_tokens[i].unsqueeze(0)
        tags = list(dataset_labels[i].numpy())
        Y_true += tags

        Y_batch_pred_weights = model(batch_tokens).squeeze(0)
        Y_batch_pred = torch.argmax(Y_batch_pred_weights, 1)
        Y_pred += list(Y_batch_pred.numpy())

    return get_scores(Y_true, Y_pred)

Uczenie modelu:

In [71]:
NUM_EPOCHS = 5

In [72]:
for i in range(NUM_EPOCHS):
    lstm.train()
    # for i in tqdm(range(500)):
    for i in tqdm(range(len(train_labels))):
        batch_tokens = train_tokens_ids[i].unsqueeze(0)
        tags = train_labels[i].unsqueeze(1)

        predicted_tags = lstm(batch_tokens)

        optimizer.zero_grad()
        loss = criterion(predicted_tags.squeeze(0), tags.squeeze(1))

        loss.backward()
        optimizer.step()

    lstm.eval()
    print(eval_model(validation_tokens_ids, validation_labels, lstm))

  0%|          | 0/14041 [00:00<?, ?it/s]

  0%|          | 0/3250 [00:00<?, ?it/s]

(0.4973622179818161, 0.515052888527258, 0.5060529922338968)


  0%|          | 0/14041 [00:00<?, ?it/s]

  0%|          | 0/3250 [00:00<?, ?it/s]

...

  0%|          | 0/3250 [00:00<?, ?it/s]

(0.7720238820519069, 0.7364872718819017, 0.753837001784652)


  0%|          | 0/14041 [00:00<?, ?it/s]

  0%|          | 0/3250 [00:00<?, ?it/s]

(0.8183865412637435, 0.7181215854934325, 0.7649826646854879)


Ewaluacja:

In [73]:
eval_model(validation_tokens_ids, validation_labels, lstm)

  0%|          | 0/3250 [00:00<?, ?it/s]

(0.8183865412637435, 0.7181215854934325, 0.7649826646854879)

In [74]:
eval_model(test_tokens_ids, test_labels, lstm)

  0%|          | 0/3453 [00:00<?, ?it/s]

(0.7458321146534074, 0.628698224852071, 0.6822742474916388)

## Zadanie 3

Sklonuj repozytorium https://git.wmi.amu.edu.pl/kubapok/en-ner-conll-2003

Stwórz model *sequence labelling* realizujący zadanie NER, oparty o dowolną rekurencyjną sieć neuronową (możesz wzorować się na przykładzie z zajęć).

W plikach dev-0/out.tsv oraz test-A/out.tsv umieść wyniki predykcji dla dev-0/in.tsv i test-A/in.tsv odpowiednio.
Do ewaluacji wykorzystaj narzędzie GEval (https://gitlab.com/filipg/geval):

    wget https://gonito.net/get/bin/geval
    chmod u+x geval
    ./geval --help

Liczba punktów uzyskanych za zadanie zależy od uzyskanej wartości accuracy na zbiorze `test-A` (wynik zaokrąglony w górę):

    points = math.ceil(accuracy * 7.0)

⚠️ W systemie Moodle proszę załączyć plik `test-A/out.tsv` oraz link do repozytorium z rozwiązaniem zadania.
 